###  dataset https://www.consumerfinance.gov/data-research/
https://www.consumerfinance.gov/data-research/consumer-complaints/

What the consumers were complaining in the financial product and service market? 
Data from these complaints help us understand the financial marketplace and protect consumers.

In [0]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from scipy import stats
import seaborn as sns

from pyspark import SparkContext
from pyspark.sql import Window
from pyspark.sql import SQLContext
#from pyspark.sql.functions import col, udf
import pyspark.sql.functions as F
from pyspark.sql.functions import split, explode
#from pyspark.sql.functions import regexp_replace, trim, col, lower
from pyspark.sql.types import IntegerType
from pyspark.sql.types import StructType, StructField, DateType, IntegerType, StringType, DoubleType, TimestampType

from pyspark.ml.feature import Tokenizer, RegexTokenizer

NLP related installation and import

In [0]:
#word cloud
!pip install wordcloud
from wordcloud import WordCloud 
from wordcloud import WordCloud, STOPWORDS 
import matplotlib.pyplot as plt 

In [0]:
#!/bin/bash
!pip install nltk
!pip install --upgrade pip
!nltk.downloader all

import nltk
from pyspark.ml.feature import Tokenizer, StopWordsRemover
from nltk.stem.snowball import SnowballStemmer
nltk.download('punkt')
nltk.download('twitter_samples')
nltk.download('averaged_perceptron_tagger')
nltk.download('maxent_ne_chunker')
nltk.download('words')
nltk.download('ieer')
nltk.download('stopwords')
#stopwords = set(STOPWORDS) 
stopwords = nltk.corpus.stopwords.words('english')
#########
from pyspark.ml import Pipeline
from pyspark.ml.feature import StringIndexer


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data] Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package twitter_samples to /root/nltk_data...
[nltk_data] Unzipping corpora/twitter_samples.zip.
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data] /root/nltk_data...
[nltk_data] Unzipping taggers/averaged_perceptron_tagger.zip.
[nltk_data] Downloading package maxent_ne_chunker to
[nltk_data] /root/nltk_data...
[nltk_data] Unzipping chunkers/maxent_ne_chunker.zip.
[nltk_data] Downloading package words to /root/nltk_data...
[nltk_data] Unzipping corpora/words.zip.
[nltk_data] Downloading package ieer to /root/nltk_data...
[nltk_data] Unzipping corpora/ieer.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data] Unzipping corpora/stopwords.zip.

#### 1.1 Data acquisition
- download [json format datasource](http://files.consumerfinance.gov/ccdb/complaints.json.zip) to local storage and unzip. Upload the unzipped json file to DBFS
- read json file and partion by 
- create dellta table. Delta Engine is a high performance, Apache Spark compatible query engine that provides an efficient way to process data in data lakes including data stored in open source Delta Lake. Delta Engine optimizations accelerate data lake operations, supporting a variety of workloads ranging from large-scale ETL processing to ad-hoc, interactive queries.

In [0]:
#dbutils.fs.rm('dbfs:/FileStore/tables/complaints-1.json',True)
display(dbutils.fs.ls("dbfs:/FileStore/tables/"))

path name size dbfs:/FileStore/tables/complaints.csv complaints.csv 1233411049 dbfs:/FileStore/tables/complaints.json complaints.json 1942366519 dbfs:/FileStore/tables/exercise_pyspark_dataframe.ipynb exercise_pyspark_dataframe.ipynb 30542 dbfs:/FileStore/tables/flight_model/ flight_model/ 0 dbfs:/FileStore/tables/flight_weather.csv flight_weather.csv 431664555

#####1.1.1 Pick up few data for observation.
Here we can see the data fields consists of three parts, according to these columns, we're going to do data transformation.
- date columns: yyyy-mm-dd format
- some categorical columns: adding numeric index for these columns
- descriptive column: nlp analysis
- location related columns: geological visualization

In [0]:
# have quick view of the content of this json file
dbutils.fs.head("dbfs:/FileStore/tables/complaints.json", 4096)  


[Truncated to first 4096 bytes]
Out[29]: '[\n{"date_received": "2019-09-24", "product": "Debt collection", "sub_product": "I do not know", "issue": "Attempts to collect debt not owed", "sub_issue": "Debt is not yours", "complaint_what_happened": "transworld systems inc. \\nis trying to collect a debt that is not mine, not owed and is inaccurate.", "company_public_response": "", "company": "TRANSWORLD SYSTEMS INC", "state": "FL", "zip_code": "335XX", "tags": "", "consumer_consent_provided": "Consent provided", "submitted_via": "Web", "date_sent_to_company": "2019-09-24", "company_response": "Closed with explanation", "timely": "Yes", "consumer_disputed": "N/A", "complaint_id": "3384392"},\n{"date_received": "2019-09-19", "product": "Credit reporting, credit repair services, or other personal consumer reports", "sub_product": "Credit reporting", "issue": "Incorrect information on your report", "sub_issue": "Information belongs to someone else", "complaint_what_happened": "", "company_public_response": "Company has responded to the consumer and the CFPB and chooses not to provide a public response", "company": "Experian Information Solutions Inc.", "state": "PA", "zip_code": "15206", "tags": "", "consumer_consent_provided": "Consent not provided", "submitted_via": "Web", "date_sent_to_company": "2019-09-20", "company_response": "Closed with non-monetary relief", "timely": "Yes", "consumer_disputed": "N/A", "complaint_id": "3379500"},\n{"date_received": "2019-11-08", "product": "Debt collection", "sub_product": "I do not know", "issue": "Communication tactics", "sub_issue": "Frequent or repeated calls", "complaint_what_happened": "Over the past 2 weeks, I have been receiving excessive amounts of telephone calls from the company listed in this complaint. The calls occur between XXXX XXXX and XXXX XXXX to my cell and at my job. The company does not have the right to harass me at work and I want this to stop. It is extremely distracting to be told 5 times a day that I have a call from this collection agency while at work.", "company_public_response": "", "company": "Diversified Consultants, Inc.", "state": "NC", "zip_code": "275XX", "tags": "", "consumer_consent_provided": "Consent provided", "submitted_via": "Web", "date_sent_to_company": "2019-11-08", "company_response": "Closed with explanation", "timely": "Yes", "consumer_disputed": "N/A", "complaint_id": "3433198"},\n{"date_received": "2021-01-28", "product": "Credit reporting, credit repair services, or other personal consumer reports", "sub_product": "Credit reporting", "issue": "Problem with a credit reporting company\'s investigation into an existing problem", "sub_issue": "Investigation took more than 30 days", "complaint_what_happened": "", "company_public_response": "", "company": "EQUIFAX, INC.", "state": "FL", "zip_code": "33432", "tags": "", "consumer_consent_provided": "", "submitted_via": "Web", "date_sent_to_company": "2021-01-28", "company_response": "Closed with explanation", "timely": "Yes", "consumer_disputed": "N/A", "complaint_id": "4102456"},\n{"date_received": "2019-09-15", "product": "Debt collection", "sub_product": "Other debt", "issue": "Attempts to collect debt not owed", "sub_issue": "Debt was result of identity theft", "complaint_what_happened": "Pioneer has committed several federal violations against me, a Private law abiding Federally Protected Consumer. Each violation is a statutory cost of {$1000.00} each, which does not include my personal cost and fees which shall be determined for taking time to address these issues. Violations committed against me include but not limited to : ( 1 ) Violated 15 USC 1692c ( a ) ; Communication without prior consent, expressed permission. ( 2 ) Violated 15 USC 1692d ; Harass and oppressive use of intercourse about an alleged debt. ( 3 ) Violated 15 USC 1692d ( l ) ; Attacking my reputation, accusing me of owing an alleged debt to you. ( 4 ) Violated 15 USC 1692e ( 9 ) ; Use/distribution of communication with aut

In [0]:
from pyspark.sql.types import DateType
file_name = '/FileStore/tables/complaints.json'
#For a regular multi-line JSON file, set the multiLine option to true.
schema = """ `date_received`  DATE, 
`product`  STRING, 
`sub_product`  STRING, 
`issue`  STRING, 
`sub_issue`  STRING, 
`complaint_what_happened`  STRING, 
`company_public_response`  STRING, 
`company`  STRING, 
`state`  STRING, 
`zip_code`  STRING, 
`tags`  STRING, 
`consumer_consent_provided`  STRING, 
`submitted_via`  STRING, 
`date_sent_to_company`  DATE, 
`company_response`  STRING, 
`timely`  STRING, 
`consumer_disputed`  STRING, 
`complaint_id`  STRING""" 

df = spark.read.option("multiline",True).\
  json("/FileStore/tables/complaints.json", schema=schema)

In [0]:
df = df.withColumn("complaint_id", df["complaint_id"].cast("bigint"))

In [0]:
pd.DataFrame(df.take(5), columns=df.columns).transpose()

0 
 1 
 2 
 3 
 4 
 
 
 
 
 date_received 
 2019-09-24 
 2019-09-19 
 2019-11-08 
 2019-09-15 
 2019-07-26 
 
 
 product 
 Debt collection 
 Credit reporting, credit repair services, or o... 
 Debt collection 
 Debt collection 
 Credit reporting, credit repair services, or o... 
 
 
 sub_product 
 I do not know 
 Credit reporting 
 I do not know 
 Other debt 
 Credit reporting 
 
 
 issue 
 Attempts to collect debt not owed 
 Incorrect information on your report 
 Communication tactics 
 Attempts to collect debt not owed 
 Problem with a credit reporting company's inve... 
 
 
 sub_issue 
 Debt is not yours 
 Information belongs to someone else 
 Frequent or repeated calls 
 Debt was result of identity theft 
 Their investigation did not fix an error on yo... 
 
 
 complaint_what_happened 
 transworld systems inc. \nis trying to collect... 
 
 Over the past 2 weeks, I have been receiving e... 
 Pioneer has committed several federal violatio... 
 Previously, on XX/XX/XXXX, XX/XX/XXXX, and XX/... 
 
 
 company_public_response 
 
 Company has responded to the consumer and the ... 
 
 
 Company has responded to the consumer and the ... 
 
 
 company 
 TRANSWORLD SYSTEMS INC 
 Experian Information Solutions Inc. 
 Diversified Consultants, Inc. 
 Pioneer Capital Solutions Inc 
 Experian Information Solutions Inc. 
 
 
 state 
 FL 
 PA 
 NC 
 CA 
 CA 
 
 
 zip_code 
 335XX 
 15206 
 275XX 
 925XX 
 914XX 
 
 
 tags 
 
 
 
 
 
 
 
 consumer_consent_provided 
 Consent provided 
 Consent not provided 
 Consent provided 
 Consent provided 
 Consent provided 
 
 
 submitted_via 
 Web 
 Web 
 Web 
 Web 
 Web 
 
 
 date_sent_to_company 
 2019-09-24 
 2019-09-20 
 2019-11-08 
 2019-09-15 
 2019-07-26 
 
 
 company_response 
 Closed with explanation 
 Closed with non-monetary relief 
 Closed with explanation 
 Closed with explanation 
 Closed with explanation 
 
 
 timely 
 Yes 
 Yes 
 Yes 
 Yes 
 Yes 
 
 
 consumer_disputed 
 N/A 
 N/A 
 N/A 
 N/A 
 N/A 
 
 
 complaint_id 
 3384392 
 3379500 
 3433198 
 3374555 
 3319331

In [0]:
print((df.count(), len(df.columns)))

(1449162, 18)

#### 1.2 Data cleansing
- Check date range, only keep the sent date before 2020 (exclude the influence of covid-19)
- Delete data withought primary key (Complaint ID)
-  N/A value in **Consumer disputed**
- remove empty states
- check states

In [0]:
#https://blog.csdn.net/sinat_26917383/article/details/80500349
# display(df.groupBy("state").count())
# delete null rows of these columns, delete empty state and an outlier
df = df.filter("date_received<'2020-01-01' and state !='' and state!='UNITED STATES MINOR OUTLYING ISLANDS' ").\
  dropna(subset=['complaint_id', 'issue','product','date_received','company','state','submitted_via'])
#total record count  1.9 m

#### 1.3 Data transformation

##### 1.3.1 Convert categorical columns to numeric 
- process all categorical columns, generate _index column. Converts these columns of string values to label indexes.

In [0]:
#these are some categorical string columns, add according code column to make it easier to process
"""
cat_columns = ['product','sub_product',\
               'issue','sub_issue',\
               'submitted_via','company','company_response',\
               'consumer_consent_provided','timely']
"""           
cat_columns = ['product','sub_product',\
               'issue','sub_issue']
#pipeline
indexers = [StringIndexer(inputCol=column, outputCol=column+"_index") for column in cat_columns ]
pipeline = Pipeline(stages=indexers)
#coresponding *_index columns are added to the new dataframe
df_convert = pipeline.fit(df).transform(df)

In [0]:
#the basic abstraction in Spark. Represents an immutable, partitioned collection of elements that can be operated on in parallel
#categorical column
df_convert.select('product').distinct().rdd.map(lambda r: r[0]).collect()
df_convert.select('sub_product').distinct().rdd.map(lambda r: r[0]).collect()

Out[56]: ['Other (i.e. phone, health club, etc.)',
 'Loan',
 'Savings account',
 'Conventional home mortgage',
 'CD (Certificate of Deposit)',
 'Lease',
 'Home equity loan or line of credit',
 'Money order',
 'Other mortgage',
 'Other special purpose card',
 'Gift card',
 'Payday loan debt',
 'Checking account',
 'Virtual currency',
 'Mobile or digital wallet',
 'Government benefit payment card',
 'I do not know',
 'Payday loan',
 'Title loan',
 'Foreign currency exchange',
 'Other banking product or service',
 'Other bank product/service',
 'General-purpose credit card or charge card',
 'International money transfer',
 'Other personal consumer report',
 'Other debt',
 'Mortgage debt',
 'Student prepaid card',
 'Transit card',
 'Mortgage',
 'Auto',
 'Vehicle lease',
 'Federal student loan servicing',
 'Domestic (US) money transfer',
 'Personal line of credit',
 'Other type of mortgage',
 'Traveler’s/Cashier’s checks',
 'Credit card debt',
 'Vehicle loan',
 'General-purpose prepaid card',
 'Payroll card',
 'Federal student loan debt',
 'ID prepaid card',
 'Installment loan',
 'Credit reporting',
 'Conventional fixed mortgage',
 'Store credit card',
 'Credit repair',
 'Reverse mortgage',
 '(CD) Certificate of deposit',
 'Home equity loan or line of credit (HELOC)',
 'Pawn loan',
 'Auto debt',
 'Government benefit card',
 'FHA mortgage',
 'Federal student loan',
 'Credit repair services',
 'General purpose card',
 'Debt settlement',
 'Conventional adjustable mortgage (ARM)',
 'Cashing a check without an account',
 'Credit card',
 '',
 'Private student loan',
 'Gift or merchant card',
 'Medical',
 'VA mortgage',
 'Check cashing service',
 'Refund anticipation check',
 'Non-federal student loan',
 'Check cashing',
 'Electronic Benefit Transfer / EBT card',
 'Private student loan debt',
 'Medical debt',
 "Traveler's check or cashier's check",
 'Second mortgage',
 'Mobile wallet']

In [0]:
display(df_convert)

date_received product sub_product issue sub_issue complaint_what_happened company_public_response company state zip_code tags consumer_consent_provided submitted_via date_sent_to_company company_response timely consumer_disputed complaint_id product_index sub_product_index issue_index sub_issue_index 2019-09-24 Debt collection I do not know Attempts to collect debt not owed Debt is not yours transworld systems inc. 
is trying to collect a debt that is not mine, not owed and is inaccurate. TRANSWORLD SYSTEMS INC FL 335XX Consent provided Web 2019-09-24 Closed with explanation Yes N/A 3384392 2.0 5.0 6.0 8.0 2019-09-19 Credit reporting, credit repair services, or other personal consumer reports Credit reporting Incorrect information on your report Information belongs to someone else Company has responded to the consumer and the CFPB and chooses not to provide a public response Experian Information Solutions Inc. PA 15206 Consent not provided Web 2019-09-20 Closed with non-monetary relief Yes N/A 3379500 0.0 0.0 0.0 1.0 2019-11-08 Debt collection I do not know Communication tactics Frequent or repeated calls Over the past 2 weeks, I have been receiving excessive amounts of telephone calls from the company listed in this complaint. The calls occur between XXXX XXXX and XXXX XXXX to my cell and at my job. The company does not have the right to harass me at work and I want this to stop. It is extremely distracting to be told 5 times a day that I have a call from this collection agency while at work. Diversified Consultants, Inc. NC 275XX Consent provided Web 2019-11-08 Closed with explanation Yes N/A 3433198 2.0 5.0 8.0 11.0 2019-09-15 Debt collection Other debt Attempts to collect debt not owed Debt was result of identity theft Pioneer has committed several federal violations against me, a Private law abiding Federally Protected Consumer. Each violation is a statutory cost of {$1000.00} each, which does not include my personal cost and fees which shall be determined for taking time to address these issues. Violations committed against me include but not limited to : ( 1 ) Violated 15 USC 1692c ( a ) ; Communication without prior consent, expressed permission. ( 2 ) Violated 15 USC 1692d ; Harass and oppressive use of intercourse about an alleged debt. ( 3 ) Violated 15 USC 1692d ( l ) ; Attacking my reputation, accusing me of owing an alleged debt to you. ( 4 ) Violated 15 USC 1692e ( 9 ) ; Use/distribution of communication with authorization or approval. ( 5 ) Violated 15 USC 1692f ( l ) ; Attempting to collect a debt unauthorized by an agreement between parties. Pioneer Capital Solutions Inc CA 925XX Consent provided Web 2019-09-15 Closed with explanation Yes N/A 3374555 2.0 8.0 6.0 15.0 2019-07-26 Credit reporting, credit repair services, or other personal consumer reports Credit reporting Problem with a credit reporting company's investigation into an existing problem Their investigation did not fix an error on your report Previously, on XX/XX/XXXX, XX/XX/XXXX, and XX/XX/XXXX I requested that Experian send me a copy of the verifiable proof they have on file showing that the XXXX account they have listed on my credit report is actually mine. On XX/XX/XXXX and XX/XX/XXXX, instead of sending me a copy of the verifiable proof that I requested, Experian sent me a statement which reads, " The information you disputed has been verified as accurate. '' Experian also failed to provide me with the method of " verification. '' Since Experian neither provided me with a copy of the verifiable proof, nor did they delete the unverified information, I believe they are in violation of the Fair Credit Reporting Act and I have been harmed as a result. I have again, today, sent my fourth and final written request that they verify the account, and send me verifiable proof that this account is mine, or that they delete the unverified account. If they do not, my next step is to pursue a remedy through litigation. Company has responded to the consumer

##### 1.3.2 date columns 
- generate date type columns and drop the old string columns

In [0]:
from pyspark.sql.functions import to_timestamp,date_format

df_convert = df_convert\
  .withColumn("received_date", df_convert['date_received']).drop('date_received') \
  .withColumn('sent_date', df_convert['date_sent_to_company']).drop('date_sent_to_company')\
#  .withColumn('sent_year', date_format(df_convert['date_sent_to_company'],'y'))\
#  .withColumn('sent_month', date_format(df_convert['date_sent_to_company'],'M'))\

#print(df_convert.schema)

In [0]:
# save cleaned data to table.
df_convert.createOrReplaceTempView('t_complaints')

In [0]:
display(df_convert)

product sub_product issue sub_issue complaint_what_happened company_public_response company state zip_code tags consumer_consent_provided submitted_via company_response timely consumer_disputed complaint_id product_index sub_product_index issue_index sub_issue_index received_date sent_date Debt collection I do not know Attempts to collect debt not owed Debt is not yours transworld systems inc. 
is trying to collect a debt that is not mine, not owed and is inaccurate. TRANSWORLD SYSTEMS INC FL 335XX Consent provided Web Closed with explanation Yes N/A 3384392 2.0 5.0 6.0 8.0 2019-09-24 2019-09-24 Credit reporting, credit repair services, or other personal consumer reports Credit reporting Incorrect information on your report Information belongs to someone else Company has responded to the consumer and the CFPB and chooses not to provide a public response Experian Information Solutions Inc. PA 15206 Consent not provided Web Closed with non-monetary relief Yes N/A 3379500 0.0 0.0 0.0 1.0 2019-09-19 2019-09-20 Debt collection I do not know Communication tactics Frequent or repeated calls Over the past 2 weeks, I have been receiving excessive amounts of telephone calls from the company listed in this complaint. The calls occur between XXXX XXXX and XXXX XXXX to my cell and at my job. The company does not have the right to harass me at work and I want this to stop. It is extremely distracting to be told 5 times a day that I have a call from this collection agency while at work. Diversified Consultants, Inc. NC 275XX Consent provided Web Closed with explanation Yes N/A 3433198 2.0 5.0 8.0 11.0 2019-11-08 2019-11-08 Debt collection Other debt Attempts to collect debt not owed Debt was result of identity theft Pioneer has committed several federal violations against me, a Private law abiding Federally Protected Consumer. Each violation is a statutory cost of {$1000.00} each, which does not include my personal cost and fees which shall be determined for taking time to address these issues. Violations committed against me include but not limited to : ( 1 ) Violated 15 USC 1692c ( a ) ; Communication without prior consent, expressed permission. ( 2 ) Violated 15 USC 1692d ; Harass and oppressive use of intercourse about an alleged debt. ( 3 ) Violated 15 USC 1692d ( l ) ; Attacking my reputation, accusing me of owing an alleged debt to you. ( 4 ) Violated 15 USC 1692e ( 9 ) ; Use/distribution of communication with authorization or approval. ( 5 ) Violated 15 USC 1692f ( l ) ; Attempting to collect a debt unauthorized by an agreement between parties. Pioneer Capital Solutions Inc CA 925XX Consent provided Web Closed with explanation Yes N/A 3374555 2.0 8.0 6.0 15.0 2019-09-15 2019-09-15 Credit reporting, credit repair services, or other personal consumer reports Credit reporting Problem with a credit reporting company's investigation into an existing problem Their investigation did not fix an error on your report Previously, on XX/XX/XXXX, XX/XX/XXXX, and XX/XX/XXXX I requested that Experian send me a copy of the verifiable proof they have on file showing that the XXXX account they have listed on my credit report is actually mine. On XX/XX/XXXX and XX/XX/XXXX, instead of sending me a copy of the verifiable proof that I requested, Experian sent me a statement which reads, " The information you disputed has been verified as accurate. '' Experian also failed to provide me with the method of " verification. '' Since Experian neither provided me with a copy of the verifiable proof, nor did they delete the unverified information, I believe they are in violation of the Fair Credit Reporting Act and I have been harmed as a result. I have again, today, sent my fourth and final written request that they verify the account, and send me verifiable proof that this account is mine, or that they delete the unverified account. If they do not, my next step is to pursue a remedy through litigation. Company has responded to the consumer and the CFPB and choo

##### 1.3.2 location related columns 
- generate

#### 2.1 What are the most complained products?

##### 2.1.1 Where are the complaints from
From annually top N rank of complaints amount by states, we can see
- the amount of complaints are all increased during the analysis period
- compare to the other top-ranked states which have shown slowdown in total complaints since 2017, the FL states shows rapid growth during the period given.
- the top N ranked states chart shows that the amount of complaints in the state is proportional to that of the population.

In [0]:
#group count by year by states and save the result to temp view: t_state_count
df_state_count = sqlContext.sql("SELECT year(sent_date) as sent_year,state,count(1) AS count " + \
                  " FROM t_complaints " +\
                  " GROUP BY year(sent_date),state")

In [0]:
#save to table
df_state_count.createOrReplaceTempView('t_state_count')

In [0]:
from pyspark.sql.window import Window
 
df_state_count_rank = df_state_count.select("sent_year","state","count", F.row_number().over(Window.partitionBy(df_state_count['sent_year']).orderBy(df_state_count['count'].desc())).alias("rank")).filter("rank<6")
display(df_state_count_rank)


sent_year state count rank 2018 CA 32551 1 2018 FL 26484 2 2018 TX 24222 3 2018 NY 17091 4 2018 GA 15314 5 2015 CA 23847 1 2015 FL 15959 2 2015 TX 13405 3 2015 NY 11552 4 2015 GA 7542 5 2013 CA 16890 1 2013 FL 10641 2 2013 NY 7388 3 2013 TX 6967 4 2013 GA 4849 5 2014 CA 21508 1 2014 FL 14708 2 2014 TX 13182 3 2014 NY 10132 4 2014 GA 6276 5 2019 FL 35128 1 2019 CA 34043 2 2019 TX 25648 3 2019 NY 20362 4 2019 GA 16555 5 2020 CA 104 1 2020 FL 86 2 2020 GA 41 3 2020 TX 40 4 2020 NY 31 5 2012 CA 11550 1 2012 FL 6894 2 2012 NY 5387 3 2012 TX 3605 4 2012 GA 3336 5 2016 CA 26864 1 2016 FL 18519 2 2016 TX 15525 3 2016 NY 13363 4 2016 GA 9841 5 2011 CA 406 1 2011 FL 238 2 2011 NY 193 3 2011 TX 131 4 2011 GA 85 5 2017 CA 31694 1 2017 TX 22368 2 2017 FL 22268 3 2017 NY 15219 4 2017 GA 14754 5 2021 CA 1 1

- Show complaints distribution on the map.

In [0]:
df_state_count = sqlContext.sql("SELECT state,sum(count) AS value " + \
                  " FROM t_state_count WHERE state!='UNITED STATES MINOR OUTLYING ISLANDS' " +\
                  " GROUP BY state")
#stateRDD = sqlContext.createDataFrame(sc.parallelize())
#stateRDD.registerTempTable("test_state_table")

display(df_state_count)

state value AZ 30661 SC 22666 LA 18212 MN 15038 AA 25 NJ 53776 DC 7790 OR 14290 VA 41676 RI 4149 WY 1344 KY 10006 NH 5231 MI 34147 NV 19261 WI 14735 ID 4306 CA 199458 CT 16109 NE 3977 MT 2237 NC 45451 VT 1835 MD 40552 DE 6932 MO 20989 VI 258 IL 56510 ME 3886 GU 203 WA 27147 ND 1385 MS 8489 AL 17440 IN 16231 AE 537 OH 43557 TN 24280 IA 5640 NM 6246 PA 50424 SD 1692 NY 100718 FM 115 MH 31 TX 125093 WV 3377 GA 78593 AS 29 MA 25605 KS 6968 CO 22926 FL 150925 AK 1533 AR 7158 PW 13 OK 9037 PR 3638 AP 387 MP 34 UT 9740 HI 4464

##### 2.1.1 Top 4 complained products
- *Credit reporting, credit repair services, or other personal consumer reports*
- *Debt collection*
- *Mortgage*
- *Credit reporting*

In [0]:
df_product = sqlContext.sql("SELECT product,product_index,count(1) AS count " + \
                           " FROM t_complaints " +\
                           " GROUP BY product,product_index ORDER BY 3 DESC")
display(df_product)

product product_index count Credit reporting, credit repair services, or other personal consumer reports 0.0 318994 Mortgage 1.0 289318 Debt collection 2.0 272632 Credit reporting 3.0 139959 Credit card 4.0 88476 Bank account or service 5.0 84650 Credit card or prepaid card 6.0 63087 Student loan 7.0 55020 Checking or savings account 8.0 52161 Consumer Loan 9.0 31423 Vehicle loan or lease 10.0 14465 Money transfer, virtual currency, or money service 11.0 12246 Payday loan, title loan, or personal loan 12.0 11221 Payday loan 13.0 5523 Money transfers 14.0 5155 Prepaid card 15.0 3776 Other financial service 16.0 1039 Virtual currency 17.0 17

##### 2.2.1 Checking sub-product to see what happened.
- There are two products refer to the Credit reporting, including **Credit reporting, credit repair services, or other personal consumer reports** and **Credit reporting**, and the sub product is **Credit reporting** or **Other personal consumer report** . Let's focus on credit report, and try to find what happened about this issue.
- 
Over 99% of these complaints are about Credit reporting

In [0]:
#filter those are credit report or consumer report related complaints
df_complaints_report = sqlContext.sql("SELECT product, sub_product,sub_product_index,count(1) AS count " + \
                           " FROM t_complaints " +\
                           " WHERE product_index in (0,3) " +\
                           " AND sub_product_index in (0,1,32) " +\
                           " GROUP BY product,sub_product,sub_product_index ORDER BY 4 DESC")
#save to table
df_complaints_report.createOrReplaceTempView('t_complaints_report')
display(df_complaints_report)

product sub_product sub_product_index count Credit reporting, credit repair services, or other personal consumer reports Credit reporting 0.0 313331 Credit reporting 1.0 139959 Credit reporting, credit repair services, or other personal consumer reports Other personal consumer report 32.0 4557

In [0]:
report_complaint_count = df_complaints_report.select(F.sum('count')).collect()[0][0]
#pd_count = pd.DataFrame(report_complaint_count, columns=report_complaint_count.columns
# almost 40% complaints is about credit reporting
#what's the proportion of these complaints, 32%, big
print((report_complaint_count/df_convert.count())*100)

31.593914275974665

##### 2.2.3 What's the issues about **Credit reporting**?
Among the nearly 40% of total complaints, what's the issues in it.
- There are many kinds of issues of these complaints data. Let's try to extract essential words from the detail of these issues.

In [0]:
df_story = sqlContext.sql(\
                          " SELECT complaint_what_happened as content " +\
                          " FROM t_complaints WHERE " +\
                          " product_index in (0,3) AND " +\
                          " sub_product_index in (0,1,32) AND " +\
                          " complaint_what_happened IS NOT NULL AND " +\
                          " complaint_what_happened !='' ")

In [0]:
tokenizer = Tokenizer(inputCol="content", outputCol="words")

regexTokenizer = RegexTokenizer(inputCol="content", outputCol="words", pattern="\\W")
# alternatively, pattern="\\w+", gaps(False)
countTokens = udf(lambda words: len(words), IntegerType())

tokenized = tokenizer.transform(df_story)
tokenized.select("content", "words")\
    .withColumn("tokens", countTokens(F.col("words"))).show(truncate=False)


regexTokenized = regexTokenizer.transform(df_story)
regexTokenized.select("content", "words") \
    .withColumn("tokens", countTokens(F.col("words"))).show(truncate=False)


+----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

In [0]:
#remove x masks
stopwords = np.append(stopwords,["x","xx","xxx","xxxx","xxxxx"])


In [0]:
#remove stop words
stopWordsRemover = StopWordsRemover(inputCol='words', outputCol='clean_words' ,stopWords=stopwords)
df_words_cleaned = stopWordsRemover.transform(regexTokenized)
display(df_words_cleaned)

content words clean_words Previously, on XX/XX/XXXX, XX/XX/XXXX, and XX/XX/XXXX I requested that Experian send me a copy of the verifiable proof they have on file showing that the XXXX account they have listed on my credit report is actually mine. On XX/XX/XXXX and XX/XX/XXXX, instead of sending me a copy of the verifiable proof that I requested, Experian sent me a statement which reads, " The information you disputed has been verified as accurate. '' Experian also failed to provide me with the method of " verification. '' Since Experian neither provided me with a copy of the verifiable proof, nor did they delete the unverified information, I believe they are in violation of the Fair Credit Reporting Act and I have been harmed as a result. I have again, today, sent my fourth and final written request that they verify the account, and send me verifiable proof that this account is mine, or that they delete the unverified account. If they do not, my next step is to pursue a remedy through litigation. List(previously, on, xx, xx, xxxx, xx, xx, xxxx, and, xx, xx, xxxx, i, requested, that, experian, send, me, a, copy, of, the, verifiable, proof, they, have, on, file, showing, that, the, xxxx, account, they, have, listed, on, my, credit, report, is, actually, mine, on, xx, xx, xxxx, and, xx, xx, xxxx, instead, of, sending, me, a, copy, of, the, verifiable, proof, that, i, requested, experian, sent, me, a, statement, which, reads, the, information, you, disputed, has, been, verified, as, accurate, experian, also, failed, to, provide, me, with, the, method, of, verification, since, experian, neither, provided, me, with, a, copy, of, the, verifiable, proof, nor, did, they, delete, the, unverified, information, i, believe, they, are, in, violation, of, the, fair, credit, reporting, act, and, i, have, been, harmed, as, a, result, i, have, again, today, sent, my, fourth, and, final, written, request, that, they, verify, the, account, and, send, me, verifiable, proof, that, this, account, is, mine, or, that, they, delete, the, unverified, account, if, they, do, not, my, next, step, is, to, pursue, a, remedy, through, litigation) List(previously, requested, experian, send, copy, verifiable, proof, file, showing, account, listed, credit, report, actually, mine, instead, sending, copy, verifiable, proof, requested, experian, sent, statement, reads, information, disputed, verified, accurate, experian, also, failed, provide, method, verification, since, experian, neither, provided, copy, verifiable, proof, delete, unverified, information, believe, violation, fair, credit, reporting, act, harmed, result, today, sent, fourth, final, written, request, verify, account, send, verifiable, proof, account, mine, delete, unverified, account, next, step, pursue, remedy, litigation) Hello This complaint is against the three credit reporting companies. XXXX, Trans Union and XXXX. I noticed some discrepencies on my credit report so I put a credit freeze with XXXX.on XX/XX/2019. I then notified the three credit agencies previously stated with a writtent letter dated XX/XX/2019 requesting them to verifiy certain accounts showing on my report They were a Bankruptcy and a bank account from XXXX XXXX XXXX. 
The response from XXXX and XXXX was that it was verified through their third partner XXXX. That can not be correct because I have a Freeze on my XXXX XXXX account since XX/XX/XXXX. which no one can obtain my report for anything until I unfreeze it. 
I wrote XXXX and XXXX a second letter and mailed them on XX/XX/2019 telling them that they have lied when they said that they verified the two accounts in question using XXXX because I have a freeze on my account and when I called XXXX on XX/XX/2019 they stated that no one has requested or attempted access to my account this year. I told them that they are in violation of my consumer rights and demand that these two accounts be removed from my report immediately. Only XXXX wrote back a letter dated XX/XX/2019 stati

In [0]:
df_clean_words = df_words_cleaned.select(explode(df_words_cleaned.clean_words)).alias('word').filter("length('word')>2")
#df_clean_words.createOrReplaceTempView('t_words')
#display(df_clean_words)

In [0]:
display(df_clean_words)

In [0]:
#word count
df_word_count = df_clean_words.groupby('col').count()

In [0]:
display(df_word_count.orderBy('count', ascending=False))

col count credit 414246 report 226117 account 201171 information 173044 reporting 132991 accounts 85101 consumer 78616 00 73254 equifax 71526 company 59979 removed 55466 payment 53834 file 53184 would 53002 dispute 52442 debt 51675 never 51572 sent 50469 experian 50354 please 49179 letter 49092 also 48873 late 47987 reported 47704 inquiry 46052 remove 44700 bureaus 44600 received 44537 time 44062 date 42795 identity 42519 loan 41698 number 39968 agency 39950 days 39726 paid 39269 name 38179 transunion 37726 collection 37031 due 36348 inquiries 35631 theft 35454 still 35065 request 34858 get 34686 card 34462 payments 34388 balance 34000 score 33785 told 33515 one 33003 3 32865 reports 32783 address 32394 section 32326 proof 32037 disputed 31395 called 31271 made 31082 back 30693 2 30616 fcra 30046 contacted 27743 even 27138 fraudulent 27022 provide 26835 since 26821 inaccurate 26548 years 26013 verified 26004 complaint 25429 requested 25225 creditor 25192 1 25111 copy 24958 agencies 24754 bank 24728 law 24669 bankruptcy 24022 said 23877 fraud 23863 several 23286 phone 23240 amount 22993 listed 22834 original 22779 could 22709 bureau 22679 items 22598 30 22461 investigation 22000 closed 21938 n 21937 asked 21904 times 21874 verify 21862 see 21751 filed 21657 showing 21276 without 21022 correct 20957 provided 20809 act 20731 like 20500 incorrect 20399 need 20392 well 20114 companies 20043 pay 20040 opened 19918 deleted 19912 attached 19816 contact 19683 call 19657 fair 19614 past 19562 following 19446 last 19319 full 19241 security 18949 help 18906 know 18883 immediately 18872 block 18729 personal 18720 months 18647 hard 18446 mail 18286 mine 18085 documents 17866 issue 17749 documentation 17724 stated 17550 delete 17460 response 17445 must 17364 negative 17337 mortgage 17256 claim 16761 however 16661 three 16607 send 16523 court 16408 verification 16378 2018 16377 two 16157 new 16147 month 15914 open 15911 day 15879 violation 15653 4 15602 service 15530 item 15524 may 15492 business 15379 make 15311 want 15226 status 15038 stating 15033 error 15003 letters 14998 matter 14955 first 14926 5 14867 federal 14852 charge 14707 required 14706 regarding 14659 tried 14642 yet 14527 loans 14251 notice 14224 victim 14071 submitted 13924 within 13889 nothing 13790 accurate 13779 another 13673 used 13634 year 13496 record 13486 done 13382 history 13338 contract 13235 social 13198 updated 13059 state 12942 home 12925 able 12894 certified 12889 2019 12785 services 12626 check 12556 show 12521 car 12412 failed 12338 take 12337 data 12300 online 12288 shall 12285 trying 12190 current 12159 requesting 12143 police 12055 fact 12025 c 11962 via 11868 statement 11727 result 11720 financial 11607 cfpb 11540 every 11410 alleged 11375 case 11368 2017 11323 multiple 11274 anything 11274 us 11181 someone 11179 unauthorized 11178 right 11175 money 11076 shows 10921 creditors 10896 belong 10886 legal 10839 spoke 10817 email 10798 b 10794 signed 10712 signature 10672 went 10629 per 10598 states 10577 15 10549 put 10270 person 10254 process 10216 disputes 10205 validation 10175 rights 10164 many 10073 advised 9919 authorized 9847 false 9810 department 9800 bill 9632 found 9618 different 9604 freeze 9591 going 9553 placed 9543 got 9527 thank 9527 7 9526 public 9512 collections 9495 give 9461 written 9460 wrong 9447 records 9428 update 9404 already 9393 recently 9306 receive 9257 asking 9240 customer 9196 breach 9158 ago 9156 investigate 9153 problem 9153 access 9131 informed 9045 system 9030 later 9000 keep 8961 knowledge 8920 way 8841 unable 8831 today 8831 representative 8821 notified 8791 according 8783 owe 8772 charged 8753 use 8751 continue 8750 action 8674 believe 8538 refused 8525 student 8497 ever 8347 disputing 8343 applied 8332 6 8305 auto 8293 inquires 8259 evidence 8247 alert 8240 blocked 8182 resolve 8155 consumers 8074 line 8074 dates 8060 old 8005 0 7989 find 7949 noticed 7883 writing 7869 ftc 7819 claims 7812 obtain 7809 id 7787 getting 7765 s

In [0]:

# Generate a word cloud image
#wordcloud = WordCloud(stopwords=stopwords, background_color="white").generate(story_str)
wcloud = WordCloud().generate_from_frequencies(story_str)

# make figure to plot
plt.figure()
# plot words
plt.imshow(wcloud, interpolation="bilinear")
# remove axes
plt.axis("off")
# show the result
plt.show()

In [0]:

def apply_blob(sentence):
    temp = TextBlob(sentence).sentiment[0]
    if temp == 0.0:
        return 0.0 # Neutral
    elif temp >= 0.0:
        return 1.0 # Positive
    else:
        return 2.0 # Negative
sentiment = udf(apply_blob)
df_story.withColumn("sentiment", sentiment(df_story['complaint_what_happened'])).show()
      

##### 2.2.4 Which company contributed this issue most?
- Check how this issue distributed in within these companies. Have they dealed these complaints timely?
TRANSUNION INTERMEDIATE HOLDINGS, INC. , Experian Information Solutions Inc. and EQUIFAX, INC. have the highest count of complaints on this issue. By google these companies, we can find these are established for over 30 years financial company. Is this because they have a big consumer group?

##### 2.2.9 Let's generate words cloud to have a clear insight about the consumers' complaints
- split issue, sub_issue and narrative fields

In [0]:
pd_issue = pd.DataFrame(df_issue, columns= ['issue'])
tuples = [tuple(x) for x in pd_issue['issue']]
wordcloud = WordCloud().generate_from_frequencies(dict(tuples))

##### Which company contributed this issue most?
- Check how this issue distributed in within these companies. Have they dealed these complaints timely?
TRANSUNION INTERMEDIATE HOLDINGS, INC. , Experian Information Solutions Inc. and EQUIFAX, INC. have the highest count of complaints on this issue. By google these companies, we can find these are established for over 30 years financial company. Is this because they have a big consumer group?

In [0]:
df_company_issue = sqlContext.sql("SELECT company,count(1) as count, " + \
                           " round((sum(IF(timely='No', 1, 0))/count(1))*100,2) as delay_percent " +\
                           " FROM t_complaints " +\
                           " WHERE PRODUCT='Credit reporting, credit repair services, or other personal consumer reports' " +\
                           " AND sub_product='Credit reporting' " +\
                           " AND issue='Incorrect information on your report' AND sub_issue='Information belongs to someone else' "\
                           " GROUP BY company")
display(df_company_issue)

###### How can we look further?
- Using web crawler, check the user amount of this company. 
- Checking the narrative, generating words cloud to see.
- From time aspect, check whether these issued have been fixed. 

These top 3 companies all have timely response, so this time let's only focus on the amount about this issue during these years. 
The line chart shows, from 2015 by now, this issue has been increased gradually instead of improved. Since 2020, the complaints amount increased greatly.

In [0]:
df_company_improve = sqlContext.sql("SELECT company,date_received,to_timestamp(date_received, 'yyyy-MM') as received_ym," + \
                           " count(1) as total "         
                           " FROM t_complaints " +\
                           " WHERE PRODUCT='Credit reporting, credit repair services, or other personal consumer reports' " +\
                           " AND sub_product='Credit reporting' " +\
                           " AND issue='Incorrect information on your report' AND sub_issue='Information belongs to someone else' "\
                           " AND ((company='TRANSUNION INTERMEDIATE HOLDINGS, INC.')  "
                           " OR (company='Experian Information Solutions Inc.')  "
                           " OR (company='EQUIFAX, INC.'))  "
                           " GROUP BY company,date_received,to_timestamp(date_received, 'yyyy-MM')")

display(df_company_improve)

#### By taking some sampling data, we have seen what the data looks like.
- **complaint_what_happened** is the description of what that consumer complained. By applying nlp related analysis, can we find the sentiment of these records. This is all about complaints, but there usually exists different levels of severity. If we can analysis these levels, it might be used for the future classification.
- Check the columns which have these standard items
- **date_received** and **date_sent_to_company** for applying time series analysis

| Column Name               | Remark   |
|-------------------------|----------|
| company                   | any change or converge|
| company_public_response   | is it standard?|
| company_response          | standard item|
| complaint_id              | primary key  |
| complaint_what_happened   | story|
| consumer_consent_provided | standard item|
| consumer_disputed         | standard item|
| date_received             | date yyyy-mm-dd|
| date_sent_to_company      | date yyyy-mm-dd|
| issue                     | standard item|
| product                   | standard item|
| state                     | CA|
| sub_issue                 | standard item|
| sub_product               | standard item|
| submitted_via             | standard item|
| tags                      | ?|
| timely                    | standard item|
| zip_code                  | is it standard?|

In [0]:
df.count()

- Clearing text from punctuation (regexp_replace)
 - Tokenization (Tokenizer)
 - Delete stop words (StopWordsRemover)
 - Stematization (SnowballStemmer)
 - Filtering short words (udf)

In [0]:


sentenceDataFrame = spark.createDataFrame([
    (0, "Hi I heard about Spark"),
    (1, "I wish Java could use case classes"),
    (2, "Logistic,regression,models,are,neat")
], ["id", "sentence"])

tokenizer = Tokenizer(inputCol="sentence", outputCol="words")

regexTokenizer = RegexTokenizer(inputCol="sentence", outputCol="words", pattern="\\W")
# alternatively, pattern="\\w+", gaps(False)

countTokens = udf(lambda words: len(words), IntegerType())

tokenized = tokenizer.transform(sentenceDataFrame)
tokenized.select("sentence", "words")\
    .withColumn("tokens", countTokens(col("words"))).show(truncate=False)

regexTokenized = regexTokenizer.transform(sentenceDataFrame)
regexTokenized.select("sentence", "words") \
    .withColumn("tokens", countTokens(col("words"))).show(truncate=False)

In [0]:
#get 100 sample data and remove id is null. backwords execution
dfProduct100 = dfProduct.dropna().limit(100)
type(dfProduct100)

In [0]:


sentenceDataFrame = dfProduct100

regexTokenizer = RegexTokenizer(inputCol="product", outputCol="words", pattern="\\W")
countTokens = udf(lambda words: len(words), IntegerType())

regexTokenized = regexTokenizer.transform(sentenceDataFrame)
regexTokenized.select("product", "words") \
    .withColumn("tokens", countTokens(col("words"))).show(truncate=False)


In [0]:
#regexTokenized = regexTokenized.withColumn('words', concat_ws(' ', 'words'))
#regexTokenized.show(11)

In [0]:
#convert list column 'words' to string
#from pyspark.sql.functions import col, concat_ws
#words_list = regexTokenized.limit(100).select('words').collect() 
#stringList = ' '.join([str(item[0]) for item in words_list ])
#stringList
#import pyspark.sql.functions.*
#dfTokenized.select(concat_ws(' ', split(dfTokenized.words)).alias('content')).collect()

In [0]:
#stopwords = set(STOPWORDS) 
comment_words = ''  
# iterate through the csv file 
#for val in regexTokenized.words: 
    # typecaste each val to string 
    # split the value 
    ##tokens = val.split() 
    # Converts each token into lowercase 
    ##for i in range(len(tokens)): 
    ##    tokens[i] = tokens[i].lower() 
      
    ##comment_words += " ".join(tokens)+" "
#    comment_words += " ".join(val)+" "
wordcloud = WordCloud(width = 800, height = 800, 
                background_color ='white', 
                min_font_size = 10).generate('credit reporting credit repair services or other personal consumer reports debt collection debt collection payday loan title loan or personal loan mortgage credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit card or prepaid card debt collection credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit card or prepaid card credit reporting credit repair services or other personal consumer reports vehicle loan or lease credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports checking or savings account debt collection credit reporting credit repair services or other personal consumer reports checking or savings account credit reporting credit repair services or other personal consumer reports mortgage credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports or not applying for credit recently credit card or prepaid card debt collection credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports mortgage credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports debt collection credit reporting credit repair services or other personal consumer reports credit reporting credit repair services or other personal consumer reports credit reporting credit repair services') 


In [0]:
  
# plot the WordCloud image                        
plt.figure(figsize = (8, 8), facecolor = None) 
plt.imshow(wordcloud) 
plt.axis("off") 
plt.tight_layout(pad = 0) 
plt.show() 

###NLP
-  DocumentAssembler(), one of the most essential transformers of the Spark NLP library. It’s the entry point to get your data in, and then process further with annotators. And, without linking its output to annotators in a pipeline, it has no meaning. In the following articles, we will talk about how you can apply certain NLP tasks on top of DocumentAssembler()

In [0]:
from sparknlp.base import *
documentAssembler = DocumentAssembler().setInputCol("product").setOutputCol("document").setCleanupMode("shrink")
doc_df = documentAssembler.transform(dfProduct100)
doc_df.show(10)

####flatten the document column

In [0]:
doc_df.select("document.result").take(1)
import pyspark.sql.functions as F
doc_df.withColumn("tmp",F.explode("document")).select("tmp.*").show(3)

In [0]:
wordcloud = WordCloud(width = 800, height = 800, 
                background_color ='white', 
                stopwords = stopwords, 
                min_font_size = 10).generate(stringList) 
  
# plot the WordCloud image                        
plt.figure(figsize = (8, 8), facecolor = None) 
plt.imshow(wordcloud) 
plt.axis("off") 
plt.tight_layout(pad = 0) 
plt.show() 

In [0]:
dfNarrative = dfProduct.filter("narrative IS NOT NULL")
dfNarrative.show(3)
#dfNarrative = dfProduct.select("narrative", "id").where(col("narrative").isNoNull())
#dfNarrative.show(20)

In [0]:
dfNarrative.count()

#### Where are these customers, in which way they complained.
 - using geo information to visualize the distribution of these consumers.
 - count the complaint record by source.

In [0]:
display(dfProduct)

In [0]:
#pie chart
#dfProduct.agg({'via': 'count'}).withColumnRenamed("count(via)", "via_count").show()

w = Window.partitionBy('via')
#dfProduct.groupBy('via').count().select('via', dfProduct.col('count').alias('via_count')).show(10)
#dfProduct.select('via', dfProduct.count('via').over(w).alias('via_count')).sort('via').show()

#dfProduct.withColumn('via', F.count('via').over(w)).sort('via').show()
dfVia = sqlContext.sql(\
                           "SELECT `Submitted via` AS via, " + \
                           "COUNT(`Submitted via`) OVER (PARTITION BY `Submitted via`) as via_count " + \
                           "FROM table1 ")
display(dfVia)
#dfProduct.groupBy(F.col('via')).agg(F.count('via').alias('via_count')).show()


In [0]:

dfTest = sqlContext.sql(\
                           "SELECT * FROM table1 WHERE `Complaint ID`='1471337'")
display(dfTest)

In [0]:
dfProduct.select('via', F.count('via').over(w).alias('via_count')).show()

In [0]:
display(dfProduct)

### 3 Machine Learning
- Can we predict the the sentiment of the consumers by extracting the story of these complaints.

#### 3.1 Feature processing
- Prepare features.

In [0]:
trainDF, testDF = df.randomSplit([0.8, 0.2], seed=42)
print(trainDF.cache().count()) # Cache because accessing training data multiple times
print(testDF.count())

#these are some categorical string columns, add according code column to make it easier to process
cat_columns = ['product','sub_product',\
               'issue','sub_issue',\
               'submitted_via','company','company_response',\
               'consumer_consent_provided','timely']
#pipeline
#indexers = [StringIndexer(inputCol=column, outputCol=column+"_index").fit(trainDF) for column in cat_columns ]
indexers = StringIndexer(inputCols=categoricalCols, outputCols=[x + "Index" for x in cat_columns]) 

pipeline = Pipeline(stages=indexers)
#coresponding *_index columns are added to the new dataframe
df_convert = pipeline.fit(df).transform(df)

- What's the distribution of the number of hours_per_week?
- How about education status?

In [0]:
display(trainDF.select("hours_per_week").summary())


display(trainDF
        .groupBy("education")
        .count()
        .sort("count", ascending=False))

In [0]:
display(trainDF
        .groupBy("education")
        .count()
        .sort("count", ascending=False))

#### 3.1 Definae the model
- Define the model.

#### 3.2 Buil the pipeline
- pipeline.....

#### 3.3 Evaluate the model
- pipeline.....

#### 3.4 Hyperparameter tuning
- tunning.....

#### 3.5 Make predictions and evaluate model performance
- prediction.....